# Lab 1 :

# I Exact simulation of one-dimensional neuronal model

## 1 Wiener process with drift :
$$
dV(t) = Idt + \sigma dB(t),\quad V(0) = V_{0}
$$
Exact distribution of (V(t)) : (cf lecture)
$$
V(t_{i})= V(t_{i-1}) + I\Delta + \mathcal{N}(0,\Delta \sigma^{2})
$$

In [24]:
import numpy as np 
import matplotlib.pyplot as plt
import math
import plotly
#from plotly import __version__
py=plotly.offline
go =plotly.graph_objs
plotly.offline.init_notebook_mode()

def histogram(data,title,dataName,Y_name=[""]):
    trace= []
    if Y_name ==[""]:
        Y_name = [""]*len(data);
        
    for i in range(0,len(data)):
        histo = go.Histogram(
            x=data[i],
            histnorm='probability',
            opacity=0.5,
            #xbins=dict(start=min(data[i])-0.25, size= 5, end= max(data[i])+0.25),
            name=Y_name[i]
        )
        trace.append(histo)
    layout = go.Layout(
    title=title,
    xaxis=dict(
        title=dataName
    ),
    yaxis=dict(
        title='Count'
    ),
    barmode='stack',
    bargap=0,
    bargroupgap=0
    )
    fig = go.Figure(data=trace, layout=layout)
    #py.plot(fig, filename='histogram/histogramIsBooking'+data_name+'Histogram.html')
    py.iplot(fig)
    
def scatter(X_name,Y,Y_name,title,X=0,histo=0):
    if X == 0 :
        X = [ x for x in range(0,len(Y[0]))];
    data = []
    for i in range(0,len(Y)):
        data.append(go.Scatter(
        x=X,
        y=Y[i],
        mode = 'lines',
        name = Y_name[i]
    ))
    layout = go.Layout(
        title=title,
        xaxis=dict(
            title=X_name,
            titlefont=dict(
                family='Courier New, monospace',
                size=18,
                color='#7f7f7f'
            )
        ),
        yaxis=dict(
            title='value',
            titlefont=dict(
                family='Courier New, monospace',
                size=18,
                color='#7f7f7f'
            )
        )
    )
    
    fig = go.Figure(data=data, layout=layout)
    py.iplot(fig)

In [2]:
def Wiener(delta, numberOfTrials, I, V0, sigma,graph=""):
    Vlist = []
    sigmaName = []
    for j in sigma:
        V=[V0];
        for i in range(1,numberOfTrials):
            V.append(V[i-1] + I*delta + np.random.normal(0,(math.sqrt(delta))*j))
        Vlist.append(V)  
        sigmaName.append("sigma = "+str(j))
    if graph=="":
        scatter("time",Vlist,sigmaName,"Wiener process ")
    return Vlist;
  #      plt.plot(V,label="Wiener process with sigma = "+str(j))
  #      plt.title("Wiener process")
  #      plt.xlabel("time")
  #      plt.xlabel("Wiener process")
  #      plt.legend(loc='best')
  #  plt.show()
    

In [140]:
Wiener(0.0001,1000,-10,-65,[1,10,20])

[[-65,
  -65.00106269278942,
  -65.00320141694068,
  -64.99710554642853,
  -65.00772303252853,
  -65.0170522594886,
  -65.03238097090869,
  -65.03727800270279,
  -65.02868131553184,
  -65.02503338521632,
  -65.02439371938443,
  -65.02870852303454,
  -65.01088477541818,
  -65.01515173153619,
  -65.00074442292494,
  -65.01372681486832,
  -65.03431224519872,
  -65.02234035115247,
  -65.00509240824299,
  -65.0102095789491,
  -65.00854313254322,
  -65.0155836821484,
  -65.01680518297937,
  -65.0227771537763,
  -65.03897892993294,
  -65.0059704960045,
  -65.00120181781357,
  -64.99850704210589,
  -65.00252499092727,
  -65.0240318432961,
  -65.04963895574603,
  -65.0512782726978,
  -65.05593606290775,
  -65.06035794823048,
  -65.06697528252556,
  -65.06360205873357,
  -65.04781575998713,
  -65.05859201161513,
  -65.0515767974426,
  -65.05099092271087,
  -65.05747644161698,
  -65.05142066324468,
  -65.04490833079393,
  -65.05438057763482,
  -65.06373678624765,
  -65.07120658512052,
  -65.07170

## 2 Ornstein-Uhlenbeck process : 
$$
dV(t) = (-\frac{V(t) - \alpha}{\tau})dt + \sigma dB(t),\quad V(0) = V_{0},\quad with\quad \alpha = V_{0} + \tau I
$$
Exact distribution of (V(t)) : (cf lecture)
$$
V(t_{i})= V(t_{i-1})\exp(\frac{-\Delta}{\tau}) +\tau (\frac{V_{0}}{\tau} + I)(1-\exp(\frac{-\Delta}{\tau}) + \mathcal{N}(0,\sigma \sqrt{\frac{\tau}{2}(1-\exp(-2\frac{\Delta}{\tau}})
$$

In [4]:
def OU(delta, numberOfTrials,tau, I, V0, sigma,S):
    V=[V0];
    spikeDistrib = [0]
    spikingTime = 0
    spikes = []
    for i in range(1,numberOfTrials):
        Vi = V[i-1]*math.exp((-delta/tau)) + (V0/tau + I)*tau*(1-math.exp(-(delta)/tau)) + np.random.normal(0,(math.sqrt((tau/2)*(1-math.exp(-2*(delta)/tau))))*sigma)
        if Vi > S :
            V.append(V0);
            if spikes == []:
                spikeDistrib.append( i);
            else:
                spikeDistrib.append( i-spikes[-1]);
            spikes.append(i)

        else:
            V.append(Vi);
            
    scatter("time",[V],['sigma = '+str(sigma)],"Ornstein-Uhlenbeck process ")
    histogram([spikeDistrib],'Spike Distribution','time')
    return V
    #plt.subplot(211)
    #plt.plot(V,label="Ornstein-Uhlenbeck process with sigma = "+str(sigma))
    #plt.title("Ornstein-Uhlenbeck process")
    #plt.xlabel("time")
    #plt.ylabel("Ornstein-Uhlenbeck process")
    #for i in range(#0,len(spikes)):
    #    plt.axvline(spikes[i],color='r')
    #plt.legend()
    #plt.subplot(212)
#
    #plt.hist(spikeDistrib,bins=len(set(spikeDistrib)))
    ##print(spikeDistrib)
    #plt.title("Spike Distribution")
    #plt.xlabel("time")
    #plt.ylabel("occurences")/tau + I
    #plt.show()

In [37]:
V = OU(0.01,20000,0.5,50,-65,10,-45)

In [38]:
V = OU(0.01,20000,0.5,20,-65,10,-45)

# II Approximate simulation of one-dimensional neuronal model

## 1 Ornstein-Uhlenbeck process :

### Euler scheme for the OU process :

Set $ (V_{t})$ a solution of $ dV(t) = (-\frac{V(t) - \alpha}{\tau})dt + \sigma dB(t),\quad V(0) = V_{0},\quad with\quad \alpha = V_{0} + \tau I $.

We want to approximate $(V_{t})$ on [0,T]. We start by descretizing the time interval : $0=t_{0}<t_{1}<...<t_{N}=T$.

Let $\Delta_{j} = t_{j+1} - t_{j} \simeq dt \rightarrow B_{t_{j+1}} - B_{t_{j}} \simeq dB_{t}$. 

The Euler-Maruyama approximation of $(V_{t})$  is $(X_{t})$ defined by : 
\begin{equation}
\begin{split}
 X_{0} &= V_{0}\\
 X_{t_{1}} - X_{t_{0}} &= (-\frac{X(t_{0}) - \alpha}{\tau})(t_{1}-t_{0}) + \sigma (B_{t_{1}} - B_{t_{0}})\\
 &=\quad ... \\
\forall j=1..(N-1):\quad X_{t_{j+1}} &= X_{t_{j}} + (-\frac{X(t_{j}) - \alpha}{\tau})\Delta_{j} + \sigma(B_{t_{j+1}} - B_{t_{j}})\\
\end{split}
\end{equation}
With : $ (B_{t_{j+1}} - B_{t_{j}}) \sim \mathcal{N}(0,\Delta_{j})$


In [39]:
def EulerOU(delta, numberOfTrials,tau, I, V0, sigma,S):
    X=[V0];
    alpha = V0 + tau*I;
    spikeDistrib = [0]
    spikingTime = 0
    spikes = []
    for i in range(1,numberOfTrials):
        Xi = X[i-1] + ((-X[i-1] + alpha)/tau)*delta + sigma*np.random.normal(0,math.sqrt(delta))
        if Xi > S :
            X.append(V0);
            if spikes == []:
                spikeDistrib.append( i);
            else:
                spikeDistrib.append( i-spikes[-1]);
            spikes.append(i)
        else:
            X.append(Xi);
            
    scatter("time",[X],['sigma = '+str(sigma)],"Euler scheme : Ornstein-Uhlenbeck process ")    
    histogram([spikeDistrib],'Spike Distribution','time')
    return X

In [40]:
 X = EulerOU(0.01,20000,0.5,50,-65,10,-45)

In [12]:
diff = []
for i in range(1,len(X)):
    diff.append(V[i] - X[i])

In [13]:
scatter("time",[diff],[str(10)],"Euler scheme vs Ornstein-Uhlenbeck process ")    

## 2 Feller process :

### Euler scheme for the OU process :

Set $ (V_{t})$ a solution of $ dV(t) = (-\frac{V(t) - \alpha}{\tau})dt + \sigma\sqrt{V_{t} - V_{I}} dB(t),\quad V(0) = V_{0},\quad with\quad \alpha = V_{0} + \tau I $.

We want to approximate $(V_{t})$ on [0,T]. We start by descretizing the time interval : $0=t_{0}<t_{1}<...<t_{N}=T$.

Let $\Delta_{j} = t_{j+1} - t_{j} \simeq dt \rightarrow B_{t_{j+1}} - B_{t_{j}} \simeq dB_{t}$. 

The Euler-Maruyama approximation of $(V_{t})$  is $(X_{t})$ defined by : 
\begin{equation}
\begin{split}
 X_{0} &= V_{0}\\
 X_{t_{1}} - X_{t_{0}} &= (-\frac{X(t_{0}) - \alpha}{\tau})(t_{1}-t_{0}) + \sigma\sqrt{X_{t_{j}} - V_{I}} (B_{t_{1}} - B_{t_{0}})\\
 &=\quad ... \\
\forall j=1..(N-1):\quad X_{t_{j+1}} &= X_{t_{j}} + (-\frac{X(t_{j}) - \alpha}{\tau})\Delta_{j} + \sigma\sqrt{X_{t_{j}} - V_{I}}(B_{t_{j+1}} - B_{t_{j}})\\
\end{split}
\end{equation}
With : $ (B_{t_{j+1}} - B_{t_{j}}) \sim \mathcal{N}(0,\Delta_{j})$

In [51]:
def EulerFeller(delta, numberOfTrials,tau, I, V0,VI, sigma,S):
    alpha = V0 + tau*I;
    VIname=[]
    Xlist=[]
    spikeDistribList = []
    for j in range(0,len(VI)):
        X=[V0];
        spikeDistrib = [0]
        spikingTime = 0
        spikes = []
        VIname.append("VI = "+str(VI[j]));
        for i in range(1,numberOfTrials):
            if X[i-1] - VI[j] < 0:
                Xi = X[i-1] + ((-X[i-1] + alpha)/tau)*delta 
            else:
                Xi = X[i-1] + ((-X[i-1] + alpha)/tau)*delta + sigma*math.sqrt(X[i-1] - VI[j])*np.random.normal(0,math.sqrt(delta))
            if Xi > S :
                X.append(V0);
                if spikes == []:
                    spikeDistrib.append( i);
                else:
                    spikeDistrib.append( i-spikes[-1]);
                spikes.append(i)
            else:
                X.append(Xi);
        Xlist.append(X);
        spikeDistribList.append(spikeDistrib);
            
    scatter("time",Xlist,VIname,"Euler scheme : Feller process ")    
    for i in range(len(VIname)):
        histogram([spikeDistribList[i]],'Spike Distribution for '+str(VIname[i]),'time')
    return X

In [52]:
X = EulerFeller(0.01, 20000,0.5, 50, -65,[-70], 10,-45)

In [58]:
X = EulerFeller(0.001, 5000,0.5, 50, -65,[-140, -90,-80,-70,-60], 10,-45)

## 3 Approximate solution of multi-dimensional neuronal model :

### Elliptic FitzHugh Nagumo :



# Lab 2 :

# 1 Wiener Process with drift :

In [3]:
X = Wiener(0.0001, 10000, -10, -65, [10])

In [21]:
def WienerMLE(delta,numberOfTrials,sigma,X):
    In = 1/(numberOfTrials*delta)*(sum(X[1:]) - sum(X[:-1]))
    elem = np.array(X[1:]) - np.array(X[:-1]) - delta*In
    sigman2 = (1/numberOfTrials*delta)*(sum(elem**2))
    return In, sigman2;
    

In [8]:
def WienerAndMLE(delta, numberOfTrials, I, V0, sigma):
    X = Wiener(delta, numberOfTrials, I, V0, sigma,'no')
    In, sigman2 = WienerMLE(delta,numberOfTrials,sigma,X[0])
    return In, sigman2;

In [20]:
A = np.array([1,2,3])


14

In [189]:
 In, sigman2 = WienerAndMLE(0.0001, 100, -10, -65, [10])
print(In,math.sqrt(sigman2))

-132.21429807044842 0.13089215508974394


In [22]:
InList = []
sigman2List = []
for i in range(100):
    In , sigman2 = WienerAndMLE(0.0001, 10000, -10, -65, [10])
    InList.append(In);
    sigman2List.append(sigman2)
print(sum(InList)/le
      
      n(InList),sum(sigman2List)/len(sigman2List))

-10.044205229255603 9.99212822033e-07


# Lab 3 : 

# 1 MCMC for a one dimensional distribution : 

In [140]:
X = []
V = []
X.append(-1) 
phi = -0.1
tau = 1
sigma = 0.1

In [141]:
for i  in range(1,3):
    X.append(phi*X[i-1] + np.random.normal(0,tau))
for i in range(3):
    V.append(X[i] + np.random.normal(0,sigma))

In [127]:
rho = 0.4
q = np.random.normal(0,rho)

In [75]:
def density(x,X,V):
    return math.exp(-1/(2*(tau**2))*((x-phi*X[0])**2 + (X[2]-phi*x)**2 + ((tau/phi)**2)*(V[1]-x)**2))

In [81]:
def acceptance(xc,x1,X,V):
    alpha = density(xc,X,V)/density(x1,X,V)
    return min(1,alpha) 

In [148]:
def MCMCMH(numberOfIterations, X,V):
    X1 = []
    acceptanceRate = 0
    X1.append(V[1] -4 + np.random.normal(0,rho))
    for i in range(1,numberOfIterations):
        X1c = X1[i-1] + np.random.normal(0,rho)
        alpha = acceptance(X1c,X1[i-1],X,V);
        if (np.random.random() < alpha):
            X1.append(X1c)
            acceptanceRate +=1 ;
        else:
            X1.append(X1[i-1])
            
    scatter("time",[X1],['name'],"Metropolis-Hastings")
    histogram([X1],'Distribution','')
    return X1,acceptanceRate/numberOfIterations;
            
        
    

In [143]:
X[1]

-0.0992628855018706

In [149]:
X1,acceptanceRate = MCMCMH(10000,X,V)
print(acceptanceRate)
print("mean X1 =",sum(X1[-1000:])/len(X1[-1000:]))

0.2963
mean X1 = -0.1424713593045097
